백업의 중요성은 아무리 강조해도 지나치지 않습니다. 오늘 멀쩡하던 하드가 내일은 멀쩡하리라는 보장이 없기 때문이죠.

전문적으로 백업하는 툴도 존재하지만 여기서는 백업의 정책 결정 방법 및 tar 의 스냅샷 기능을 이용한 증분백업과 cron 을 이용해 백업의 자동화하는 방법을 알아보기로하겠습니다.

# 백업용어

* 풀 백업 (full backup): 자신이 백업하고자 하는 대상의 전체를 백업하는 방법
* 증분 백업 (incremental backup): 원본 데이터와 비교하여 원본데이터에 추가되어진 데이터만 백업하는 방법

# 백업정책

백업에 들어가기전에 염두해두어야 할 사항들(인터넷에서 펌~)

* 어떤 파일들을 백업할 것인가?
백업은 시스템에 어떤 위험이나 재난이 닥쳤을 때 중요한 데이터를 안전하게 보호하기 위해 하는 것이다. 어떤 데이터가 중요한지 파악하고 어떤 데이터를 백업할지 결정하는 것은 각자 시스템에 있는 데이터용도와 가변성에 따라 다를 것이다. 하지만 일반적으론 중요한 데이터베이스등 주로 가변적인 데이터를 백업하는 것에 초점을 둘 것이라 생각한다. 즉 가변성이 떨어지는 애플리케이션이나 시스템 파일들을 매일 백업할 필요는 없다는 것이다. 물론 시간과 능력이 된다면 모든 시스템 전체를 백업 받는게 가장 좋을 것이다.

* 백업할 위치가 어디 인가?
각각의 서버에 보면 설정 파일이라든지 실시간으로 계속 생성하는 파일들의 위치를 파악하는게 중요하다.

* 시스템 파일이 얼마나 자주 변경하는가?
시스템 파일을 자세히 살펴보면 내용이 변경되거나 생성되는 것을 볼 수 있다.

* 누가 어디서 파일을 백업할 것인가?
시스템 관리자가 항상 시스템 앞에 있다면 계속 살펴볼면서 백업할 수 있지만 시스템 관리자당 보통 수십대씩 관리하기 때문에 현실적으로 그렇지 못하다. 보통은 시스템 관리자가 먼저 시스템 상태를 파악하 뒤 크론(cron)이 라는 작업 스테쥴러를 실행해 시스템 본체가 아닌 다른 곳에 있는 저장 매체를 택해 원격지에서 백업을 실행한다.

* 어느 위치에 자료를 복구할 것인가?
자료복구는 백업할 때 그 파일 위치에 복구하는 게 가장 현명한 방법이다.

* 복구할 파일을 얼마나 빠르게 복구해야 하는가?
시스템 관리자는 항상 신속 정확해야 한다. 백업 파일을 시스템에 복구할때는 많은 사용자들이 피해를 최대한 피하기 위해 신속하고 정확하게 복구를 완료해야 할 것이다.

# tar 이용방법

## tar
테이프 생성을 위한 유틸리티로서 바이너리 데이터를 처리할 수 있습니다. 또한 여러 디렉토리를 아카이브로 묶을 수 있으며 링크를 포함하는 디렉토리들을 전송할 수 있으면서도 파일의 소유권과 액세스 퍼미션 등도 그대로 보존할 수 있는 장점이 있습니다.

간단한 tar의 사용법( tar의 플래그)
c : 아카이브 생성
x : 아카이브로 부터 파일 추출
t : 목차 테이블 보기
v : 상세한 정보 출력

```bash
$ cd /
$ tar -cf backup.tar home
$ gzip backup.tar
```

/home 의 하위디렉토리를 포함하여 backup.tar로 저장 하고 backup.tar.gz 이라는 파일을 생성하여 원래의 tar 아카이브보다 훨씬 더 작게 압축 

```bash
$ tar -cvf - home | gzip > backup.tar.gz 
```

을 하였을때는 tar에 따라서 v(verbose) 옵션을 stderr로 처리하지 않고 stdout으로 처리하여 문제를 일으키는 경우가 있습니다. 따라서 아카이브를 만들때는 v옵션을 빼는 것이 좋고, 아카이브를 풀때는 v 상관이 없습니다.

```bash
$ tar -tf backup.tar
```

아카이브를 풀기전에 항상 파일들의 이름을 먼저 검사합니다. 만일 아카이브 속의 파일들이 현재 디렉토리에 풀리도록 묶여 있다면, 임시 디렉토리를 새로 하나 만들고, 그곳으로 이동(cd)하여 파일들을 풀어냅니다.

### 일부 파일들만 뽑아내기

```bash
$ tar -xvf backup.tar filename
$ tar -xvf backup.tar `tar -tf backup.tar|grep filename`
```

여기서 filename은 tar의 t옵션으로 파일의 경로명까지 알아야 합니다. filename과 ./filename은 서로 다르므로 정확한 파일명을 지정해야 합니다. 

```bash
$ tar -xvf backup.tar `tar -tf backup.tar|grep filename` 
``` 

의 방법을 쓰는 것도 좋습니다.

### 절대 경로 문제

절대경로를 갖는 디렉토리 또는 파일을 복구할때 문제가 발생합니다. tar는 아카이브에 지정되어 있는 경로명으로 파일을 복구하기 때문에 파일이 복구될 곳을 변경할 수가 없습니다. 
따라서 이미 존재하는 파일을 덮어쓰거나 퍼미션 문제가 발생할 수 있습니다. 

GNU tar의 경우, 기본적으로 모든 절대 경로명을 상대경로 변경하여 아카이브를 만듭니다. --absolute-names 옵션을 사용하면 절대 경로로 아카이브를 만들게 됩니다. 
가장 좋은 방법은 아카이브를 만들때 디렉토리가 슬래시(/)나 틸드(~)로 시작하지 않도록 조심하는 것입니다.

```bash
$ tar -cf backup.tar -C / .
$ tar -cf backup.tar -C /home/smiletw . -C /home/woody ./test
```

-C 옵션은 아카이브를 생성하기 전에 /로 이동하도록 합니다. 
여러 개의 디렉토리들을 아카이브로 만들려면 -C옵션을 여러번 사용합니다.

### 아카이브에 추가하기

```bash
 $ tar -uvf backup.tar home
```

새로운 파일들만 업데이트 합니다. 
동일한 파일이 업데이트 되면 아카이브 마지막에 추가합니다. 
(테입장치에서는 중간에 넣을 수 없는 것을 감안)

## GNU tar를 이용한 풀백업 및 증분 백업

일반적으로 tar를 이용해서 아카이브를 만들면 풀백업이 됩니다. 
그러나 사용자 홈디렉토리 또는 한 파티션 전체를 백업할때는 풀 백업을 자주 사용하기 힘듭니다. 
이럴경우 풀 백업과 함께 증분 백업을 해 주는 것이 좋다. 
GNU tar는 옵션 처리만으로 손쉽게 풀백업과 증분 백업이 가능하게 해줍니다.
먼저 GNU tar의 풀 백업 및 증분 백업에 쓰이는 옵션이 2가지 있습니다. 
-G (--incremental) 옵션과 -g snapshot-file (--listed-incremental) 입니다.

-G 옵션은 예전 증분 백업 포맷으로 아카이브를 생성해 줍니다. 
이 옵션으로 생성된 아카이브에는 아카이브 내에 포함되어 있는 파일이나 디렉토리의 정보가 들어가므로 비표준 아카이브로 생성됩니다. 
따라서 GNU버젼이 아닌 tar로도 내용을 볼 수가 없게 됩니다. 

-g snapshot-file 옵션은 표준 아카이브로 생성되면서, 파일이나 디렉토리 등의 정보를 snapshot-file에 따로 저장함으로써, 표준 아카이브를 생성하게 만들어 줍니다. 

따라서  GNU tar를 이용한 풀 백업 및 증분 백업에서는 -G 옵션이 아닌 -g snapshot-file 옵션을 사용하는 것이 좋습니다.

### 풀 백업

```bash
 $ tar -g list -czvf backup.tar.gz home/
```

list 라는 snap-shot 파일이 생성됩니다. 그리고 backup.tar.gz이라는 백업된 아카이브가 생성됩니다.

### 증분 백업

```bash
 $ tar -g list -czvf backup-1.tar.gz home/
```

기존의 list 파일에서 이미 풀 백업된 내용을 확인하고, 그 이후에 변경되거나 추가되거나 삭제된 파일들을 backup-1.tar.gz에 백업합니다.

### GNU tar를 이용한 복구

먼저 풀 백업된 아카이브를 복구합니다.

```bash
$ tar -g list -xzvf backup.tar.gz
```

다음으로 증분 백업된 아카이브들 중 가장 최근에 백업한 것만 복구하면 됩니다.

```bash
$ tar -g list -xzvf backup-10.tar.gz
```

### 백업 및 복구의 유용한 옵션

**-W (--verify) 검증**
백업을 하는 도중 변경되는 파일이 있을 경우가 있습니다. 특히 풀 백업과 같이 시간이 오래 걸리는 백업의 경우 아카이브가 생성되는 동안 변경될 가능성이 높습니다. 

따라서 풀 백업의 경우 검증해주는 것이 좋습니다.

```bash
$ tar -g list -cWf backup.tar home/
```

이 경우 아카이브 생성 후, 아카이브의 내용과 실제 디렉토리의 내용과 같은지 확인합니다. 그러나 gzip으로 압축하는 -z 옵션과 같이 사용할 수 없습니다. 

따라서 검증 옵션을 사용해서 아카이브를 생성할 경우 gzip압축은 따로 해주어야 합니다.

## 백업 자동화

관리하는 서버가 별로 없다면 취미삼아 한대 한대씩 수동으로 백업해주어도 상관 없지만, 자신이 관리하는 서버가 여러대일경우 위에서 이야기한 나름대로의 백업 정책을 세워서 자동화 시켜 놓지 않는다면 백업은 불가능하게 됩니다. 

여기서는 예로 서버백업정책을 설정하고 쉘 스크립트와 Cron(크론)을 이용해 자동으로 백업이 되도록 꾸며 보겠습니다.

### 백업 정책

* 백업소스 디렉토리 : /home 전체
사용자가 많지 않고 /home 안에 웹및 디비 그리고 사용자정보를 모아 놓았기때문에 /home 전체를 백업하기로 결정 하였습니다.
* 백업타겟 디렉토리 : /juvat-backup
백업본을 보관할 디렉토리로 될수 있으면 다른 파티션을 준비하고, 여유가 된다면 다른 물리적 드라이브에 저장하는 것을 추천합니다.
* 백 업용 리모트 서버 : mirror.juvat.net
한 서버안에 모든 원본 및 백업본이 존재한다면 한번에 모든 정보를 날릴수 있으므로 FTP 를 이용해 주기적으로 리모트 서버에 백업파일을 저장합니다.
* 백업방법 : tar 를 이용한 풀백업 및 증분백업
전체 풀 백업을 뜨면서 생성한 스냅샷 파일을 이용해 증분 백업을 하는 형식으로 백업합니다.
* 백업주기 : /home 안의 상황이 실시간으로 중요한 정보가 없기때문에 1일을 주기로 백업하기로 하였습니다.

매월 1일에 풀 백업, 달의 나머지일은 증분 백업, 백업파일은 2개월치를 로컬 서버에 보관, 매일 백업본을 FTP로 리모트 서버에 백업

### 백업 쉘 스크립트 제작

예제로 실제 제작한 스크립트 소스입니다.

```bash
#!/bin/sh
#
# comafire's Backup Script
# last modify : 03.10.26
# mail : comafire@hotmail.net
#
# *.*.1 : Full Bakcup
# *.*.2~30 : Incremental Backup
# keep : 2 month
#
DATE=$(date +%y%m%d)
YY=$(date +%y)
MM=$(date +%m)
DD=$(date +%d)
BACKUPBAS=/
BACKUPSRC=./원본 디렉토리
BACKUPDST=/백업할 디렉토리
FTPBACKUPSRC=/FTP 로 보낼 원본 디렉토리
FTPBACKUPDST=받을 FTP 서버의 백업 디렉토리
FTP=IP or DomainName
FTPSCRIPT=/etc/cron.daily/BackupFtpScript
ID=Your ID
PASSWD=Your Password

case $MM in
        01) rm -f $BACKUPDST'/'$YY'11'*.*;;
        02) rm -f $BACKUPDST'/'$YY'12'*.*;;
        03) rm -f $BACKUPDST'/'$YY'01'*.*;;
        04) rm -f $BACKUPDST'/'$YY'02'*.*;;
        05) rm -f $BACKUPDST'/'$YY'03'*.*;;
        06) rm -f $BACKUPDST'/'$YY'04'*.*;;
        07) rm -f $BACKUPDST'/'$YY'05'*.*;;
        08) rm -f $BACKUPDST'/'$YY'06'*.*;;
        09) rm -f $BACKUPDST'/'$YY'07'*.*;;
        10) rm -f $BACKUPDST'/'$YY'08'*.*;;
        11) rm -f $BACKUPDST'/'$YY'09'*.*;;
        12) rm -f $BACKUPDST'/'$YY'10'*.*;;
esac
if [ $DD = "01" ]; then
        tar -g $BACKUPDST'/'$YY$MM.list -cf $BACKUPDST'/'$DATE.tar -C $BACKUPBAS $BACKUPSRC
elif [ -f $BACKUPDST'/'$YY$MM.list ]; then
        tar -g $BACKUPDST'/'$YY$MM.list -cf $BACKUPDST'/'$DATE.tar -C $BACKUPBAS $BACKUPSRC
fi
if [ -f $BACKUPDST'/'$DATE.tar ]; then
touch $FTPSCRIPT
echo user $ID $PASSWD >> $FTPSCRIPT
echo cd $FTPBACKUPDST >> $FTPSCRIPT
echo lcd $FTPBACKUPSRC >> $FTPSCRIPT
echo bin >> $FTPSCRIPT
echo prompt >> $FTPSCRIPT
echo put $DATE.tar >> $FTPSCRIPT
if [ $DD = "01" ] && [ -f $BACKUPDST'/'$YY$MM.list ]; then
        echo put $YY$MM.list >> $FTPSCRIPT
fi
echo bye >> $FTPSCRIPT
ftp -n $FTP < $FTPSCRIPT
rm -f $FTPSCRIPT
fi
```

여기서는 SFTP 대신 일반 FTP를 이용하였습니다. 보안을 위해서는 일반 FTP대신 SFTP 을 이용하는 것이 더욱 바람직 할 것입니다. 

하지만 최소한 백업용 계정을 SSH 에서 로그인 할수 없도록 PAM 을 이용해 로그인을 제한한다면 패스워드가 누출 되더라도 백업본 자체에만 접근할 수 있기 때문에 꼭 PAM 을 이용해 백업용 계정의 콘솔 접근을 제어 할 것을 권장합니다.